In [1]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import yaml
import pandas as pd
import numpy as np
from functools import partial
import multiprocessing
import tensorflow as tf
from pathlib import Path
from time import strftime
from shutil import rmtree
import matplotlib.pyplot as plt
from tqdm import tqdm
import matplotlib
matplotlib.use("TKAgg", force=True)
%matplotlib inline
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [2]:
from rtapipe.lib.utils.misc import dotdict
from rtapipe.lib.dataset.data_manager import DataManager
from rtapipe.lib.datasource.Photometry3 import OnlinePhotometry, SimulationParams
from rtapipe.lib.plotting.plotting import plot_sequences
from rtapipe.lib.models.anomaly_detector_builder import AnomalyDetectorBuilder
from rtapipe.lib.evaluation.pval import get_pval_table, get_threshold_for_sigma
from rtapipe.lib.standardanalysis.li_ma import LiMa
from rtapipe.lib.evaluation.pval import get_pval_table, get_threshold_for_sigma, get_sigma_from_ts, get_sigma_from_pvalue, get_sigma_for_ts_array

# Parameters

In [3]:
INTEGRATION_TIME=5
SCALER="minmax"

# Loading the models

In [4]:
with open("./trained_models.yaml", "r") as f:
    try:
        configs = yaml.safe_load(f)
    except yaml.YAMLError as exc:
        print(exc)
configs = [dotdict(c) for c in configs["models"]]

In [5]:
for i, config in enumerate(configs):
    if      config.name     == "AnomalyDetector_cnn_l2_u32" \
        and config.patience == 5 \
        and config.integrationtime == INTEGRATION_TIME \
        and config.scaler == SCALER:
        
        break
model_config_cnn = configs[i]
model_config_cnn.ad = AnomalyDetectorBuilder.getAnomalyDetector(name=model_config_cnn.name, timesteps=model_config_cnn.timesteps, nfeatures=model_config_cnn.nfeatures, load_model="True", training_epoch_dir=model_config_cnn.path, training=False)
model_config_cnn.pvalue_table = get_pval_table(model_config_cnn.pval_path) 
model_config_cnn.name

AnomalyDetector_cnn_l2_u32 - input shape: (5,3)


'AnomalyDetector_cnn_l2_u32'

In [6]:
for i, config in enumerate(configs):
    if      config.name     == "AnomalyDetector_rnn_l2_u32" \
        and config.patience == 5 \
        and config.integrationtime == INTEGRATION_TIME \
        and config.scaler == SCALER \
        and config.epoch == 5:
        
        break
model_config_rnn = configs[i]
model_config_rnn.ad = AnomalyDetectorBuilder.getAnomalyDetector(name=model_config_rnn.name, timesteps=model_config_rnn.timesteps, nfeatures=model_config_rnn.nfeatures, load_model="True", training_epoch_dir=model_config_rnn.path, training=False)
model_config_rnn.pvalue_table = get_pval_table(model_config_rnn.pval_path) 
model_config_rnn.name

AnomalyDetector_rnn_l2_u32 - input shape: (5,3)


'AnomalyDetector_rnn_l2_u32'

# Loading the test dataset

In [7]:
output_dir = "./logs/test_models_dataset_itime_5_d_out"

In [8]:
features_names = ["EB_0.04-0.117","EB_2-0.117-0.342","EB_0.342-1"]

In [9]:
data_manager = DataManager(output_dir)

In [10]:
dataset_id="test_itime_5_d_tsl_5_nbins_3"

In [11]:
dataset_folder = "/data01/homes/baroncelli/phd/rtapipe/scripts/ml/dataset_generation/test/itime_5_d/fits_data"
fits_files = DataManager.load_fits_data(dataset_folder, limit=250)
test_set_size = len(fits_files)

Loaded 231 files


In [12]:
sim_params = SimulationParams(runid=None, onset=250, emin=0.04, emax=1, tmin=0, tobs=500, offset=0.5, irf="North_z40_5h_LST", roi=2.5, caldb="prod5-v0.1", simtype="grb")
multiple_templates = True
add_target_region = True
integration_time = 5
number_of_energy_bins = 3
tsl = 100
threads = 30
normalize = True
#data_manager.transform_to_timeseries(fits_files, sim_params, add_target_region, integration_time=integration_time, number_of_energy_bins=number_of_energy_bins, tsl=tsl, normalize=normalize, threads=threads, multiple_templates=multiple_templates)
data_manager.load_saved_data(5, 100)

Loading cached data from run0005_ID000225_it_5_tsl_100.npy
Loading cached data from run0009_ID000191_it_5_tsl_100.npy
Loading cached data from run0013_ID000321_it_5_tsl_100.npy
Loading cached data from run0017_ID000302_it_5_tsl_100.npy
Loading cached data from run0019_ID000338_it_5_tsl_100.npy
Loading cached data from run0021_ID000373_it_5_tsl_100.npy
Loading cached data from run0023_ID000267_it_5_tsl_100.npy
Loading cached data from run0025_ID000471_it_5_tsl_100.npy
Loading cached data from run0027_ID000288_it_5_tsl_100.npy
Loading cached data from run0036_ID000168_it_5_tsl_100.npy
Loading cached data from run0037_ID000283_it_5_tsl_100.npy
Loading cached data from run0039_ID000031_it_5_tsl_100.npy
Loading cached data from run0045_ID000095_it_5_tsl_100.npy
Loading cached data from run0048_ID000219_it_5_tsl_100.npy
Loading cached data from run0050_ID000319_it_5_tsl_100.npy
Loading cached data from run0053_ID000030_it_5_tsl_100.npy
Loading cached data from run0058_ID000423_it_5_tsl_100.n

In [13]:
assert len(data_manager.data) == test_set_size

## Plot some samples

In [14]:
for template in list(data_manager.data.keys())[0:5]:
    data_manager.plot_timeseries(template, data_manager.data[template], 1, sim_params, output_dir, labels=features_names)

Produced: logs/test_models_dataset_itime_5_d_out/template_run0005_ID000225_trial_0_2022-12-07 17:21:30.635522.png
Saved: ./logs/test_models_dataset_itime_5_d_out/template_run0005_ID000225_trial_0_2022-12-07 17:21:30.635522.png
Produced: logs/test_models_dataset_itime_5_d_out/template_run0009_ID000191_trial_0_2022-12-07 17:21:32.835244.png
Saved: ./logs/test_models_dataset_itime_5_d_out/template_run0009_ID000191_trial_0_2022-12-07 17:21:32.835244.png
Produced: logs/test_models_dataset_itime_5_d_out/template_run0013_ID000321_trial_0_2022-12-07 17:21:35.199415.png
Saved: ./logs/test_models_dataset_itime_5_d_out/template_run0013_ID000321_trial_0_2022-12-07 17:21:35.199415.png
Produced: logs/test_models_dataset_itime_5_d_out/template_run0017_ID000302_trial_0_2022-12-07 17:21:38.438876.png
Saved: ./logs/test_models_dataset_itime_5_d_out/template_run0017_ID000302_trial_0_2022-12-07 17:21:38.438876.png
Produced: logs/test_models_dataset_itime_5_d_out/template_run0019_ID000338_trial_0_2022-12-0

# TESTING

In [15]:
data_manager.load_scaler(model_config_rnn.scaler_path) # model_config_rnn.scaler_path or model_config_cnn.scaler_path

In [16]:
sub_window_size = 5

In [17]:
test_all_x, test_all_y = data_manager.get_test_set_all_templates(verbose=False, onset=250, integration_time=integration_time, sub_window_size=sub_window_size, stride=1)

[2022-12-07 17:21:43.198210] Total x shape shape: (22176, 5, 3)
[2022-12-07 17:21:43.198264] Total y shape shape: (22176,)


# RNN

## Standard metrics - 3 sigma threshold

In [18]:
SIGMA_THRESHOLD = 3

In [19]:
sigma_threshold = get_threshold_for_sigma(model_config_rnn.pvalue_table, SIGMA_THRESHOLD)
model_config_rnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_rnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_rnn.pvalue_table, model_config_rnn.ad.threshold)} sigma")

Threshold: 0.0023888672874999 corresponding to 3.0220360846 sigma


In [20]:
print(f"************** Evaluating {model_config_rnn.name} patience={model_config_rnn.patience} **************")
metrics = model_config_rnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_rnn.ad.detection_delay(test_all_y, model_config_rnn.ad.predict(test_all_x), test_set_size, model_config_rnn.timesteps))

************** Evaluating AnomalyDetector_rnn_l2_u32 patience=5 **************
Using threshold 0.0023888672874999
accuracy 0.5049152236652237
precision 0.9913294797687862
recall 0.030303030303030304
f1 0.05880840120017146
roc_auc 0.5150133554388874
confusion_matrix [[10854, 3], [10976, 343]]
false_positive_rate 0.008670520231213872
detection_delay: 7.714285714285714


## Standard metrics - 5 sigma threshold

In [21]:
SIGMA_THRESHOLD = 5

In [22]:
sigma_threshold = get_threshold_for_sigma(model_config_rnn.pvalue_table, SIGMA_THRESHOLD)
model_config_rnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_rnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_rnn.pvalue_table, model_config_rnn.ad.threshold)} sigma")

Threshold: 0.0084223427875 corresponding to 5.0488536162 sigma


In [23]:
print(f"************** Evaluating {model_config_rnn.name} patience={model_config_rnn.patience} **************")
metrics = model_config_rnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_rnn.ad.detection_delay(test_all_y, model_config_rnn.ad.predict(test_all_x), test_set_size, model_config_rnn.timesteps))

************** Evaluating AnomalyDetector_rnn_l2_u32 patience=5 **************
Using threshold 0.0084223427875
accuracy 0.4899440836940837
precision 0.8333333333333334
recall 0.0008834702712253732
f1 0.0017650692789691995
roc_auc 0.5003496286605276
confusion_matrix [[10855, 2], [11309, 10]]
false_positive_rate 0.16666666666666666
detection_delay: 0.26406926406926406


## Sigma table

In [24]:
def crop_to_5(s):
    if s > 5: 
        s = 5.00001
    return s

In [25]:
data = {}
for template in tqdm(list(data_manager.data.keys())):
    test_x, test_y = data_manager.get_test_set(template=template, onset=250, integration_time=5, sub_window_size=5, stride=1)
    model_config_rnn.ad.predict(test_x)
    data[template] = get_sigma_for_ts_array(model_config_rnn.pvalue_table, model_config_rnn.ad.get_reconstruction_errors(), verbose=False)

sigma_table_rnn = pd.DataFrame(data, index=DataManager.get_tbin_of_sequences(96, 5, 5, 1)) 
sigma_table_rnn = sigma_table_rnn.applymap(crop_to_5)

100%|█████████████████████████████████████████| 231/231 [00:16<00:00, 14.18it/s]


In [26]:
sigma_table_rnn

run0005_ID000225  run0009_ID000191  run0013_ID000321  \
0-25             0.000000          0.000000                 0   
5-30             0.000000          0.000000                 0   
10-35            0.000000          0.000000                 0   
15-40            0.000000          0.000000                 0   
20-45            0.000000          0.000000                 0   
25-50            0.000000          0.000000                 0   
30-55            0.000000          0.000000                 0   
35-60            0.000000          0.000000                 0   
40-65            0.000000          0.000000                 0   
45-70            0.000000          0.000000                 0   
50-75            0.000000          0.000000                 0   
55-80            0.000000          0.000000                 0   
60-85            0.000000          0.000000                 0   
65-90            0.000000          0.000000                 0   
70-95            0.000000          0.000000                 0   
75-100           0.000000          0.000000                 0   
80-105           0.000000          0.000000                 0   
85-110           0.000000          0.000000                 0   
90-115           0.000000          0.000000                 0   
95-120           0.000000          0.000000                 0   
100-125          0.000000          0.000000                 0   
105-130          0.000000          0.000000                 0   
110-135          0.000000          0.000000                 0   
115-140          0.000000          0.000000                 0   
120-145          0.000000          0.000000                 0   
125-150          0.000000          0.000000                 0   
130-155          0.000000          0.000000                 0   
135-160          0.000000          0.000000                 0   
140-165          0.000000          0.000000                 0   
145-170          0.000000          0.000000                 0   
150-175          0.000000          0.000000                 0   
155-180          0.000000          0.000000                 0   
160-185          0.000000          0.000000                 0   
165-190          0.000000          0.000000                 0   
170-195          0.000000          0.000000                 0   
175-200          0.000000          0.000000                 0   
180-205          0.000000          0.000000                 0   
185-210          0.000000          0.000000                 0   
190-215          0.000000          0.000000                 0   
195-220          0.000000          0.000000                 0   
200-225          0.000000          0.000000                 0   
205-230          0.000000          0.000000                 0   
210-235          0.000000          0.000000                 0   
215-240          0.000000          0.000000                 0   
220-245          0.000000          0.000000                 0   
225-250          0.000000          0.000000                 0   
230-255          2.266801          0.000000                 0   
235-260          2.557091          0.000000                 0   
240-265          2.853188          0.000000                 0   
245-270          3.027702          0.000000                 0   
250-275          3.739494          0.000000                 0   
255-280          0.000000          0.000000                 0   
260-285          0.000000          0.000000                 0   
265-290          0.000000          0.000000                 0   
270-295          0.000000          0.000000                 0   
275-300          0.000000          0.000000                 0   
280-305          0.000000          0.000000                 0   
285-310          0.000000          0.000000                 0   
290-315          0.000000          0.000000                 0   
295-320          0.000000          0.000000                 0   
300-325          0.000000          0.000000 

# CNN

## Standard metrics - 3 sigma

In [27]:
SIGMA_THRESHOLD = 3

In [28]:
sigma_threshold = get_threshold_for_sigma(model_config_cnn.pvalue_table, SIGMA_THRESHOLD)
model_config_cnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_cnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_cnn.pvalue_table, model_config_cnn.ad.threshold)} sigma")

Threshold: 0.006506945827 corresponding to 3.0286528291 sigma


In [29]:
print(f"************** Evaluating {model_config_cnn.name} patience={model_config_cnn.patience} **************")
metrics = model_config_cnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_cnn.ad.detection_delay(test_all_y, model_config_cnn.ad.predict(test_all_x), test_set_size, model_config_cnn.timesteps))

************** Evaluating AnomalyDetector_cnn_l2_u32 patience=5 **************
Using threshold 0.006506945827
accuracy 0.4910263347763348
precision 0.9210526315789473
recall 0.0030921459492888066
f1 0.006163599542132606
roc_auc 0.5014079132620165
confusion_matrix [[10854, 3], [11284, 35]]
false_positive_rate 0.07894736842105263
detection_delay: 1.0


## Standard metrics - 5 sigma

In [30]:
SIGMA_THRESHOLD = 5

In [31]:
sigma_threshold = get_threshold_for_sigma(model_config_cnn.pvalue_table, SIGMA_THRESHOLD)
model_config_cnn.ad.threshold = sigma_threshold
print(f"Threshold: {model_config_cnn.ad.threshold} corresponding to {get_sigma_from_ts(model_config_cnn.pvalue_table, model_config_cnn.ad.threshold)} sigma")

Threshold: 0.0139048776129999 corresponding to 5.0465140766 sigma


In [32]:
print(f"************** Evaluating {model_config_cnn.name} patience={model_config_cnn.patience} **************")
metrics = model_config_cnn.ad.evaluate(test_all_x, test_all_y)
for k,v in metrics.items():
    print(k,v)
print("detection_delay:",model_config_cnn.ad.detection_delay(test_all_y, model_config_cnn.ad.predict(test_all_x), test_set_size, model_config_cnn.timesteps))

************** Evaluating AnomalyDetector_cnn_l2_u32 patience=5 **************
Using threshold 0.0139048776129999
accuracy 0.48976370851370854
precision 1.0
recall 0.0003533881084901493
f1 0.0007065265389031176
roc_auc 0.500176694054245
confusion_matrix [[10857, 0], [11315, 4]]
false_positive_rate 0.0
detection_delay: 0.030303030303030304


## Sigma table

In [33]:
data = {}
for template in tqdm(list(data_manager.data.keys())):
    test_x, test_y = data_manager.get_test_set(template=template, onset=250, integration_time=5, sub_window_size=5, stride=1)
    model_config_cnn.ad.predict(test_x)
    data[template] = get_sigma_for_ts_array(model_config_cnn.pvalue_table, model_config_cnn.ad.get_reconstruction_errors(), verbose=False)

sigma_table_cnn = pd.DataFrame(data, index=DataManager.get_tbin_of_sequences(96, 5, 5, 1))    

100%|█████████████████████████████████████████| 231/231 [00:13<00:00, 17.00it/s]


# Li&Ma

In [34]:
li_ma_data = {}
templates = list(data_manager.data.keys())
templates = []
for template in tqdm(templates):
    lima_df = LiMa.detect("binned", DataManager.get_fits_from_template(fits_files, template), temporal_bins=sigma_table_cnn.index.values, tobs=500, sigma_gt=0)
    li_ma_data[template] = lima_df["sigma"].values
lima_sigma_table = pd.DataFrame(li_ma_data, index=sigma_table_cnn.index.values)
if len(templates) > 0:
    lima_sigma_table.to_csv(Path(output_dir).joinpath("li_ma_detection_table.csv"))    

0it [00:00, ?it/s]


In [35]:
lima_sigma_table = pd.read_csv(Path(output_dir).joinpath("li_ma_detection_table.csv"), index_col=0)

In [36]:
### FIX INDEPENDENCE
sub_window_size=5
for time_bin in lima_sigma_table.index:
    if int(time_bin.split("-")[1])% (integration_time*sub_window_size) != 0:
        lima_sigma_table.loc[time_bin] = 0
lima_sigma_table

run0005_ID000225  run0009_ID000191  run0013_ID000321  \
0-25             0.845810          0.460389          0.973858   
5-30             0.000000          0.000000          0.000000   
10-35            0.000000          0.000000          0.000000   
15-40            0.000000          0.000000          0.000000   
20-45            0.000000          0.000000          0.000000   
25-50            1.063257          1.019992          0.273896   
30-55            0.000000          0.000000          0.000000   
35-60            0.000000          0.000000          0.000000   
40-65            0.000000          0.000000          0.000000   
45-70            0.000000          0.000000          0.000000   
50-75            1.136672          1.093971          0.067677   
55-80            0.000000          0.000000          0.000000   
60-85            0.000000          0.000000          0.000000   
65-90            0.000000          0.000000          0.000000   
70-95            0.000000          0.000000          0.000000   
75-100           0.817232          0.477587          0.567919   
80-105           0.000000          0.000000          0.000000   
85-110           0.000000          0.000000          0.000000   
90-115           0.000000          0.000000          0.000000   
95-120           0.000000          0.000000          0.000000   
100-125          1.324230          0.946681          0.877628   
105-130          0.000000          0.000000          0.000000   
110-135          0.000000          0.000000          0.000000   
115-140          0.000000          0.000000          0.000000   
120-145          0.000000          0.000000          0.000000   
125-150          1.284418          0.585936          0.850199   
130-155          0.000000          0.000000          0.000000   
135-160          0.000000          0.000000          0.000000   
140-165          0.000000          0.000000          0.000000   
145-170          0.000000          0.000000          0.000000   
150-175          0.655201          0.553211          1.322373   
155-180          0.000000          0.000000          0.000000   
160-185          0.000000          0.000000          0.000000   
165-190          0.000000          0.000000          0.000000   
170-195          0.000000          0.000000          0.000000   
175-200          0.340010          1.153675          0.157794   
180-205          0.000000          0.000000          0.000000   
185-210          0.000000          0.000000          0.000000   
190-215          0.000000          0.000000          0.000000   
195-220          0.000000          0.000000          0.000000   
200-225          0.076622          1.024849          0.228110   
205-230          0.000000          0.000000          0.000000   
210-235          0.000000          0.000000          0.000000   
215-240          0.000000          0.000000          0.000000   
220-245          0.000000          0.000000          0.000000   
225-250          1.691510          0.361247          0.644993   
230-255          0.000000          0.000000          0.000000   
235-260          0.000000          0.000000          0.000000   
240-265          0.000000          0.000000          0.000000   
245-270          0.000000          0.000000          0.000000   
250-275          2.316817          0.000000          1.886463   
255-280          0.000000          0.000000          0.000000   
260-285          0.000000          0.000000          0.000000   
265-290          0.000000          0.000000          0.000000   
270-295          0.000000          0.000000          0.000000   
275-300          0.000000          0.430926          0.000000   
280-305          0.000000          0.000000          0.000000   
285-310          0.000000          0.000000          0.000000   
290-315          0.000000          0.000000          0.000000   
295-320          0.000000          0.000000          0.000000   
300-325          0.460389          0.752064 

In [37]:
def crop_to_5(s):
    if s > 5: 
        s = 5.00001
    return s

In [38]:
lima_sigma_table = lima_sigma_table.applymap(crop_to_5)
lima_sigma_table

run0005_ID000225  run0009_ID000191  run0013_ID000321  \
0-25             0.845810          0.460389          0.973858   
5-30             0.000000          0.000000          0.000000   
10-35            0.000000          0.000000          0.000000   
15-40            0.000000          0.000000          0.000000   
20-45            0.000000          0.000000          0.000000   
25-50            1.063257          1.019992          0.273896   
30-55            0.000000          0.000000          0.000000   
35-60            0.000000          0.000000          0.000000   
40-65            0.000000          0.000000          0.000000   
45-70            0.000000          0.000000          0.000000   
50-75            1.136672          1.093971          0.067677   
55-80            0.000000          0.000000          0.000000   
60-85            0.000000          0.000000          0.000000   
65-90            0.000000          0.000000          0.000000   
70-95            0.000000          0.000000          0.000000   
75-100           0.817232          0.477587          0.567919   
80-105           0.000000          0.000000          0.000000   
85-110           0.000000          0.000000          0.000000   
90-115           0.000000          0.000000          0.000000   
95-120           0.000000          0.000000          0.000000   
100-125          1.324230          0.946681          0.877628   
105-130          0.000000          0.000000          0.000000   
110-135          0.000000          0.000000          0.000000   
115-140          0.000000          0.000000          0.000000   
120-145          0.000000          0.000000          0.000000   
125-150          1.284418          0.585936          0.850199   
130-155          0.000000          0.000000          0.000000   
135-160          0.000000          0.000000          0.000000   
140-165          0.000000          0.000000          0.000000   
145-170          0.000000          0.000000          0.000000   
150-175          0.655201          0.553211          1.322373   
155-180          0.000000          0.000000          0.000000   
160-185          0.000000          0.000000          0.000000   
165-190          0.000000          0.000000          0.000000   
170-195          0.000000          0.000000          0.000000   
175-200          0.340010          1.153675          0.157794   
180-205          0.000000          0.000000          0.000000   
185-210          0.000000          0.000000          0.000000   
190-215          0.000000          0.000000          0.000000   
195-220          0.000000          0.000000          0.000000   
200-225          0.076622          1.024849          0.228110   
205-230          0.000000          0.000000          0.000000   
210-235          0.000000          0.000000          0.000000   
215-240          0.000000          0.000000          0.000000   
220-245          0.000000          0.000000          0.000000   
225-250          1.691510          0.361247          0.644993   
230-255          0.000000          0.000000          0.000000   
235-260          0.000000          0.000000          0.000000   
240-265          0.000000          0.000000          0.000000   
245-270          0.000000          0.000000          0.000000   
250-275          2.316817          0.000000          1.886463   
255-280          0.000000          0.000000          0.000000   
260-285          0.000000          0.000000          0.000000   
265-290          0.000000          0.000000          0.000000   
270-295          0.000000          0.000000          0.000000   
275-300          0.000000          0.430926          0.000000   
280-305          0.000000          0.000000          0.000000   
285-310          0.000000          0.000000          0.000000   
290-315          0.000000          0.000000          0.000000   
295-320          0.000000          0.000000          0.000000   
300-325          0.460389          0.752064 

# Results

In [39]:
templates_detections = dotdict({})
for templ_det in lima_sigma_table:
    templates_detections[templ_det] = dotdict({}) 
    templates_detections[templ_det]["li_ma"] = dotdict({})
    templates_detections[templ_det]["cnn"] = dotdict({})
    templates_detections[templ_det]["rnn"] = dotdict({})

In [40]:
for templ_det in lima_sigma_table:
    detections_3s = lima_sigma_table[templ_det] >= 3
    detections_5s = lima_sigma_table[templ_det] >= 5
    templates_detections[templ_det]["li_ma"]["3s_detection"] = detections_3s.any()
    templates_detections[templ_det]["li_ma"]["5s_detection"] = detections_5s.any()
    templates_detections[templ_det]["li_ma"]["3s_detections_indexes"] = np.where(detections_3s == True)[0]
    templates_detections[templ_det]["li_ma"]["5s_detections_indexes"] = np.where(detections_5s == True)[0]

for templ_det in sigma_table_rnn:
    detections_3s = sigma_table_rnn[templ_det] >= 3
    detections_5s = sigma_table_rnn[templ_det] >= 5
    templates_detections[templ_det]["rnn"]["3s_detection"] = detections_3s.any()
    templates_detections[templ_det]["rnn"]["5s_detection"] = detections_5s.any()
    templates_detections[templ_det]["rnn"]["3s_detections_indexes"] = np.where(detections_3s == True)[0]
    templates_detections[templ_det]["rnn"]["5s_detections_indexes"] = np.where(detections_5s == True)[0]
    
for templ_det in sigma_table_cnn:
    detections_3s = sigma_table_cnn[templ_det] >= 3
    detections_5s = sigma_table_cnn[templ_det] >= 5
    templates_detections[templ_det]["cnn"]["3s_detection"] = detections_3s.any()
    templates_detections[templ_det]["cnn"]["5s_detection"] = detections_5s.any()
    templates_detections[templ_det]["cnn"]["3s_detections_indexes"] = np.where(detections_3s == True)[0]
    templates_detections[templ_det]["cnn"]["5s_detections_indexes"] = np.where(detections_5s == True)[0]    

In [41]:
def get_dd(model, templates_detections, sigma, onset_index=45):
    first_detection_indexes = []
    for template_result in templates_detections.values():
        if len(template_result[model][f"{sigma}s_detections_indexes"]) > 0:
            first_detection_indexes.append(template_result[model][f"{sigma}s_detections_indexes"][0])
    return round(np.array(first_detection_indexes).mean()-onset_index,2)

In [42]:
def get_detections_in_time(templates_detections, model, tmax, onset_index=45, sigma=5):
    first_detection_indexes = []
    for template_result in templates_detections.values():
        if len(template_result[model][f"{sigma}s_detections_indexes"]) > 0:
            first_detection_indexes.append(template_result[model][f"{sigma}s_detections_indexes"][0])
    detection_time = (np.array(first_detection_indexes)-onset_index)*integration_time
    dt_filterd = [dt for dt in detection_time if dt <= tmax]
    return len(dt_filterd)

print("i", "LiMa","RNN")
for i in range(0, 60, 5):
    if i == 0:
        continue
    print(i, get_detections_in_time(templates_detections, "li_ma", i), get_detections_in_time(templates_detections, "rnn", i))  

i LiMa RNN
5 0 2
10 0 2
15 0 2
20 0 2
25 9 2
30 9 2
35 9 2
40 9 2
45 9 2
50 12 2
55 12 2


## 3 sigma detections

In [43]:
print(f'Detected by CNN: {np.array([template_result["cnn"]["3s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("cnn",templates_detections, 3)} s')
print(f'Detected by RNN: {np.array([template_result["rnn"]["3s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("rnn",templates_detections, 3)} s')
print(f'Detected by Li&Ma: {np.array([template_result["li_ma"]["3s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("li_ma",templates_detections, 3)} s')

Detected by CNN: 16 - dd: 16.06 s
Detected by RNN: 76 - dd: 25.82 s
Detected by Li&Ma: 116 - dd: 17.46 s


In [44]:
count_rnn = 0
for template_result in templates_detections.values():
    if template_result["rnn"]["3s_detection"] and not template_result["li_ma"]["3s_detection"]:
        count_rnn += 1
print(f"Detected by RNN but not by Li&Ma: {count_rnn}")

Detected by RNN but not by Li&Ma: 12


In [45]:
count_rnn = 0
for template_result in templates_detections.values():
    if not template_result["rnn"]["3s_detection"] and template_result["li_ma"]["3s_detection"]:
        count_rnn += 1
print(f"Detected by Li&Ma but not by RNN: {count_rnn}")

Detected by Li&Ma but not by RNN: 52


## 5 sigma detections

In [46]:
print(f'Detected by CNN: {np.array([template_result["cnn"]["5s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("cnn",templates_detections, 5)} s')
print(f'Detected by RNN: {np.array([template_result["rnn"]["5s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("rnn",templates_detections, 5)} s')
print(f'Detected by Li&Ma: {np.array([template_result["li_ma"]["5s_detection"] for template_result in templates_detections.values()]).sum()} - dd: {get_dd("li_ma",templates_detections, 5)} s')

Detected by CNN: 3 - dd: 4.33 s
Detected by RNN: 5 - dd: 17.6 s
Detected by Li&Ma: 31 - dd: 21.94 s


In [47]:
count_rnn = 0
for template_result in templates_detections.values():
    if template_result["rnn"]["5s_detection"] and not template_result["li_ma"]["5s_detection"]:
        count_rnn += 1
print(f"Detected by RNN but not by Li&Ma: {count_rnn}")

Detected by RNN but not by Li&Ma: 2


In [48]:
count_rnn = 0
for template_result in templates_detections.values():
    if not template_result["rnn"]["5s_detection"] and template_result["li_ma"]["5s_detection"]:
        count_rnn += 1
print(f"Detected by Li&Ma but not by RNN: {count_rnn}")

Detected by Li&Ma but not by RNN: 28


In [49]:
matplotlib.use("TKAgg", force=True)
%matplotlib inline
from rtapipe.lib.plotting.PlotConfig import PlotConfig

def sigma_plot(template, sigma_table_model, lima_sigma_table):
    pc = PlotConfig()    
    fig, ax = plt.subplots(1,1, figsize=pc.fig_size)
    ax.plot(sigma_table_model.index.values, sigma_table_model[template], marker='o', linestyle='--', label="Anomaly Detection", zorder=1)
    ax.scatter(sigma_table_model.index.values, lima_sigma_table[template], marker='x', label="Li&Ma", zorder=10)
    ax.tick_params(axis='y', labelsize=15, width=2, grid_alpha=0.5)
    ax.tick_params(axis='x', which='major', labelsize=10)
    fig.suptitle("Detection plot")
    ax.set_title(f"Template {template}")
    ax.set_ylabel("Sigma")
    ax.set_xlabel("Timeseries")
    ax.set_ylim(0, 10)
    plt.axvline(x = 45, color = 'grey', linestyle="-.")
    plt.axhline(y = 3, color = 'orange', linestyle="-.")
    plt.axhline(y = 5, color = 'red', linestyle="-.")
    mask = [True if i%2==0 else False for i in range(len(sigma_table_model.index.values))]
    ax.set_xticks(range(0, len(sigma_table_model.index.values), 2), sigma_table_model.index.values[mask], rotation=45)
    ax.legend()
    fig.savefig(Path(output_dir).joinpath(f"detection_plot_{template}.png"), dpi=100)
    #plt.show()    
    plt.close()
templates = list(data_manager.data.keys())
    
for template in tqdm(templates):
    sigma_plot(template, sigma_table_rnn, lima_sigma_table)

100%|█████████████████████████████████████████| 231/231 [00:47<00:00,  4.87it/s]
